[![Google Colab](https://colab.research.google.com/assets/colab-badge.svg)](https://colab.research.google.com/github/idealo/image-super-resolution/blob/master/notebooks/ISR_Training_Tutorial.ipynb)

## Create the models
Import the models from the ISR package and create

- a RRDN super scaling network
- a discriminator network for GANs training
- a VGG19 feature extractor to train with a perceptual loss function

Carefully select
- 'x': this is the upscaling factor (2 by default)
- 'layers_to_extract': these are the layers from the VGG19 that will be used in the perceptual loss (leave the default if you're not familiar with it)
- 'lr_patch_size': this is the size of the patches that will be extracted from the LR images and fed to the ISR network during training time

Play around with the other architecture parameters

In [1]:
import os
os.environ["CUDA_VISIBLE_DEVICES"] = "-1"

In [2]:
# import tensorflow as tf
# # 查看gpu和cpu的数量
# gpus = tf.config.experimental.list_physical_devices(device_type='GPU')
# cpus = tf.config.experimental.list_physical_devices(device_type='CPU')
# print("Num GPUs Available: ", len((tf.config.experimental.list_physical_devices('GPU'))))
# print(gpus, cpus)

In [3]:
from ISR.models import RRDN
from ISR.models import Discriminator
from ISR.models import Cut_VGG19

In [4]:

# import torch
# print(torch.__version__)
# device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
# #返回cuda表示成功
# #或者
# print(torch.cuda.is_available())
# #返回True表示成功

In [5]:
print(os.getcwd())

d:\Master_Thesis\image-super-resolution-master\notebooks


In [6]:
lr_train_patch_size = 40#40
layers_to_extract = [5, 9]
scale = 2
hr_train_patch_size = lr_train_patch_size * scale

rrdn  = RRDN(arch_params={'C':4, 'D':3, 'G':64, 'G0':64, 'T':10, 'x':scale}, patch_size=lr_train_patch_size)
f_ext = Cut_VGG19(patch_size=hr_train_patch_size, layers_to_extract=layers_to_extract)
discr = Discriminator(patch_size=hr_train_patch_size, kernel_size=3)

In [7]:
print(os.getcwd())

d:\Master_Thesis\image-super-resolution-master\notebooks


## Give the models to the Trainer
The Trainer object will combine the networks, manage your training data and keep you up-to-date with the training progress through Tensorboard and the command line.

Here we do not use  the pixel-wise MSE but only the perceptual loss by specifying the respective weights in `loss_weights`

In [8]:
from ISR.train import Trainer
loss_weights = {
  'generator': 0.0,
  'feature_extractor': 0.0833,
  'discriminator': 0.01
}
losses = {
  'generator': 'mae',
  'feature_extractor': 'mse',
  'discriminator': 'binary_crossentropy'
} 

path = os.getcwd()#d:/Master_Thesis/image-super-resolution-master/notebooks
log_dirs = {'logs': path + '/ISR_chr/logs', 'weights': path + '/ISR_chr/weights'}

learning_rate = {'initial_value': 0.001, 'decay_factor': 0.5, 'decay_frequency': 30}
#learning_rate = {'initial_value': 0.0004, 'decay_factor': 0.5, 'decay_frequency': 30}
flatness = {'min': 0.0, 'max': 0.15, 'increase': 0.01, 'increase_frequency': 5}

trainer = Trainer(
    generator=rrdn,
    discriminator=discr,
    feature_extractor=f_ext,
    # lr_train_dir=path + '/ISR_chr/data/train_LR/',
    # hr_train_dir=path + '/ISR_chr/data/train_HR_24/',
    # lr_valid_dir=path + '/ISR_chr/data/valid_LR/',
    # hr_valid_dir=path + '/ISR_chr/data/valid_HR_2/',
    # lr_train_dir=path + '/ISR_chr/data/final_data/data_aug/train/',
    # hr_train_dir=path + '/ISR_chr/data/final_data/labels_aug/train/',
    # lr_valid_dir=path + '/ISR_chr/data/final_data/data_aug/val/',
    #hr_valid_dir=path + '/ISR_chr/data/final_data/labels_aug/val/',

    # lr_train_dir=path + '/ISR_chr/data/100_70/final2/bw70/train/',
    # lr_valid_dir=path + '/ISR_chr/data/100_70/final2/bw70/val/',

    # hr_train_dir=path + '/ISR_chr/data/100_70/final2/bw100_x2/train/',
    # hr_valid_dir=path + '/ISR_chr/data/100_70/final2/bw100_x2/val/',
    lr_train_dir=path + '/ISR_chr/data/all_data/limited_view_ISR/Interpolated_LV_WhiteBackground/data/train/',
    lr_valid_dir=path + '/ISR_chr/data/all_data/limited_view_ISR/Interpolated_LV_WhiteBackground/data/val/',

    hr_train_dir=path + '/ISR_chr/data/all_data/limited_view_ISR/Interpolated_LV_WhiteBackground/label/train/',
    hr_valid_dir=path + '/ISR_chr/data/all_data/limited_view_ISR/Interpolated_LV_WhiteBackground/label/val/',

    loss_weights=loss_weights,
    learning_rate=learning_rate,
    flatness=flatness,
    dataname='div2k',
    log_dirs=log_dirs,
    weights_generator=None,
    weights_discriminator=None,
    n_validation=200,#33,#40
)


Choose epoch number, steps and batch size and start training

In [9]:
trainer.train(
    epochs=300,#10
    steps_per_epoch=20,#20
    batch_size=4,#4
    monitored_metrics={'val_generator_PSNR_Y': 'max'}
)


Training details:
  training_parameters: 
    lr_train_dir: d:\Master_Thesis\image-super-resolution-master\notebooks/ISR_chr/data/all_data/limited_view_ISR/Interpolated_LV_WhiteBackground/data/train/
    hr_train_dir: d:\Master_Thesis\image-super-resolution-master\notebooks/ISR_chr/data/all_data/limited_view_ISR/Interpolated_LV_WhiteBackground/label/train/
    lr_valid_dir: d:\Master_Thesis\image-super-resolution-master\notebooks/ISR_chr/data/all_data/limited_view_ISR/Interpolated_LV_WhiteBackground/data/val/
    hr_valid_dir: d:\Master_Thesis\image-super-resolution-master\notebooks/ISR_chr/data/all_data/limited_view_ISR/Interpolated_LV_WhiteBackground/label/val/
    loss_weights: {'generator': 0.0, 'feature_extractor': 0.0833, 'discriminator': 0.01}
    log_dirs: {'logs': 'd:\\Master_Thesis\\image-super-resolution-master\\notebooks/ISR_chr/logs', 'weights': 'd:\\Master_Thesis\\image-super-resolution-master\\notebooks/ISR_chr/weights'}
    fallback_save_every_n_epochs: 2
    dataname:

Epoch 0/300
Current learning rate: 0.0010000000474974513
100%|██████████| 20/20 [02:17<00:00,  6.87s/it]
Epoch 0 took      137.4s


800/1 [=================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================

{'val_loss': 0.29891053821891544, 'val_generator_loss': 0.42779052, 'val_discriminator_loss': 0.14858101, 'val_feature_extractor_loss': 1.1570363, 'val_feature_extractor_1_loss': 5.984013, 'val_generator_PSNR_Y': 7.997677, 'train_d_real_loss': 0.038166426, 'train_d_real_accuracy': 1.0, 'train_d_fake_loss': 0.017561875, 'train_d_fake_accuracy': 1.0, 'train_loss': 0.14488599, 'train_generator_loss': 0.32902133, 'train_discriminator_loss': 0.018457325, 'train_feature_extractor_loss': 0.5504644, 'train_feature_extractor_1_loss': 2.9237592, 'train_generator_PSNR_Y': 10.763611}
val_generator_PSNR_Y improved from       -inf to    7.99768
Saving weights
Epoch 1/300
Current learning rate: 0.0010000000474974513
100%|██████████| 20/20 [02:22<00:00,  7.12s/it]
Epoch 1 took      142.4s


800/1 [=================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================

...

{'val_loss': 0.06803521079011261, 'val_generator_loss': 0.19580212, 'val_discriminator_loss': 0.14776586, 'val_feature_extractor_loss': 0.30363122, 'val_feature_extractor_1_loss': 1.2943894, 'val_generator_PSNR_Y': 17.60831, 'train_d_real_loss': 1.807723e-05, 'train_d_real_accuracy': 1.0, 'train_d_fake_loss': 2.0568184e-05, 'train_d_fake_accuracy': 1.0, 'train_loss': 0.038352415, 'train_generator_loss': 0.2819647, 'train_discriminator_loss': 0.1444093, 'train_feature_extractor_loss': 0.19032446, 'train_feature_extractor_1_loss': 0.69582975, 'train_generator_PSNR_Y': 15.180769}
val_generator_PSNR_Y did not improve.
Epoch 169/300
Current learning rate: 3.125000148429535e-05
Current flatness treshold: 0.15
100%|██████████| 20/20 [02:20<00:00,  7.01s/it]
Epoch 169 took      140.3s


800/1 [=================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================

{'val_loss': 0.06656295996159316, 'val_generator_loss': 0.19099426, 'val_discriminator_loss': 0.13477631, 'val_feature_extractor_loss': 0.29972583, 'val_feature_extractor_1_loss': 1.2660648, 'val_generator_PSNR_Y': 17.855152, 'train_d_real_loss': 1.4313013e-05, 'train_d_real_accuracy': 1.0, 'train_d_fake_loss': 1.0200976e-05, 'train_d_fake_accuracy': 1.0, 'train_loss': 0.05084671, 'train_generator_loss': 0.27164537, 'train_discriminator_loss': 0.14937004, 'train_feature_extractor_loss': 0.28926, 'train_feature_extractor_1_loss': 0.8956862, 'train_generator_PSNR_Y': 15.572366}
val_generator_PSNR_Y did not improve.
Epoch 170/300
Current learning rate: 3.125000148429535e-05
Current flatness treshold: 0.15
100%|██████████| 20/20 [02:20<00:00,  7.05s/it]
Epoch 170 took      141.0s


724/1 [=================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================

KeyboardInterrupt: 

In [ ]:
%load_ext tensorboard

The tensorboard extension is already loaded. To reload it, use:
  %reload_ext tensorboard


In [ ]:
#%tensorboard --logdirs= 'D:\Master_Thesis\image-super-resolution-master\notebooks/ISR_chr/logs/rrdn-C4-D3-G64-G064-T10-x2/2024-03-15_1048/'
%tensorboard --logdirs= 'D:/Master_Thesis/image-super-resolution-master/notebooks/ISR_chr/logs/rrdn-C4-D3-G64-G064-T10-x2/2024-03-15_1048/'

ERROR: Failed to launch TensorBoard (exited with 2).
Contents of stderr:
usage: tensorboard [-h] [--helpfull] [--logdir PATH] [--logdir_spec PATH_SPEC]
                   [--host ADDR] [--bind_all] [--port PORT]
                   [--purge_orphaned_data BOOL] [--db URI] [--db_import]
                   [--inspect] [--version_tb] [--tag TAG] [--event_file PATH]
                   [--path_prefix PATH] [--window_title TEXT]
                   [--max_reload_threads COUNT] [--reload_interval SECONDS]
                   [--reload_task TYPE] [--reload_multifile BOOL]
                   [--reload_multifile_inactive_secs SECONDS]
                   [--generic_data TYPE]
                   [--samples_per_plugin SAMPLES_PER_PLUGIN]
                   [--debugger_data_server_grpc_port PORT]
                   [--debugger_port PORT] [--master_tpu_unsecure_channel ADDR]
                   [--whatif-use-unsafe-custom-prediction YOUR_CUSTOM_PREDICT_FUNCTION.py]
                   [--whatif-data-dir PA

In [ ]:
%load_ext tensorboard